In [1]:
!pip install fire
!pip install peft
!pip install accelerate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.4/88.4 kB 2.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for fire: filename=fire-0.6.0-py2.py3-none-any.whl size=117031 sha256=a0980f7222027121c3d5b85ea22da12fe4c844192173c7e85d556fc632d8004a
  Stored in directory: /root/.cache/pip/wheels/d6/6d/5d/5b73fa0f46d01a793713f8859201361e9e581ced8c75e5c6a3
Successfully built fire
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.1/199.1 kB 4.9 MB/s eta 0:00:0000:01


In [2]:
import fire
import torch
import os
import sys
import time
import json
from typing import List

from transformers import (
    LlamaTokenizer,
    LlamaForCausalLM,
    AutoModelForCausalLM,
    AutoTokenizer,
    LlamaConfig
)
from peft import PeftModel
from accelerate import disk_offload

In [3]:
BASE_PROMPT = """Below is an interaction between a human and an AI fluent in English and Amharic, providing reliable and informative answers.
The AI is supposed to answer test questions from the human with short responses saying just the answer and nothing else.
Human: {}
Assistant [Amharic] : """

In [4]:
# Set the seeds for reproducibility
torch.cuda.manual_seed(42)
torch.manual_seed(42)

In [8]:
!pip install -i https://pypi.org/simple/ bitsandbytes

Looking in indexes: https://pypi.org/simple/
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.8/119.8 MB 13.9 MB/s eta 0:00:0000:0100:01
Note: you may need to restart the kernel to use updated packages.


**Don't forget to restart the kernel JO!!! 😡**

In [5]:
model = AutoModelForCausalLM.from_pretrained(
    "Johntad110/llama-2-7b-amharic-tokenizer",
    return_dict=True,
    load_in_8bit=True,
    device_map="auto",
    low_cpu_mem_usage=True,
    attn_implementation="sdpa",
    token="<HF_TOKEN>"
)

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/26.8k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.98G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/3.50G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/188 [00:00<?, ?B/s]

In [6]:
tokenizer = LlamaTokenizer.from_pretrained(
    "Johntad110/llama-2-7b-amharic-tokenizer",
    token="<HF_TOKEN>"
)

tokenizer_config.json:   0%|          | 0.00/745 [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/899k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/414 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

In [7]:
embedding_size = model.get_input_embeddings().weight.shape[0]
print(len(tokenizer), embedding_size)

51008 32000


In [8]:
if len(tokenizer) != embedding_size:
  print("resize the embedding size by the size of the tokenizer")
  model.resize_token_embeddings(len(tokenizer))

resize the embedding size by the size of the tokenizer


In [9]:
print(f"Tokenizer: {len(tokenizer)}\nEmbedding: {embedding_size}")

Tokenizer: 51008
Embedding: 32000


In [10]:
model = PeftModel.from_pretrained(model, 'Johntad110/llama-2-amharic-peft')

adapter_config.json:   0%|          | 0.00/591 [00:00<?, ?B/s]

adapter_model.bin:   0%|          | 0.00/1.75G [00:00<?, ?B/s]

In [11]:
model.eval()

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): ModulesToSaveWrapper(
          (original_module): Embedding(51008, 4096)
          (modules_to_save): ModuleDict(
            (default): Embedding(51008, 4096)
          )
        )
        (layers): ModuleList(
          (0-31): 32 x LlamaDecoderLayer(
            (self_attn): LlamaSdpaAttention(
              (q_proj): lora.Linear8bitLt(
                (base_layer): Linear8bitLt(in_features=4096, out_features=4096, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=8, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=8, out_features=4096, bias=False)
                )
                (lora_embedding_A): 

In [12]:
while True:
    user_query = input('Type question in Amharic or English: ')
    user_prompt = BASE_PROMPT.format(user_query)

    batch = tokenizer(user_prompt, return_tensors="pt")
    batch = {k: v.to("cuda") for k, v in batch.items()}

    start = time.perf_counter()

    with torch.no_grad():
        outputs = model.generate(
            **batch,
            max_new_tokens=40,
            do_sample=True,
            top_p=1.0,
            temperature=1.0,
            min_length=None,
            use_cache=True,
            top_k=1,
            repetition_penalty=1.0,
            length_penalty=1
        )

    e2e_inference_time = (time.perf_counter()-start)*1000
    print(f"the inference time is {e2e_inference_time} ms")

    output_text = tokenizer.decode(outputs[0], skip_special_tokens=True)

    print("MODEL_OUTPUT: {}".format(output_text))
    #user_prompt += output_text

Type question in Amharic or English:  አማርኛ መናገር የሚችል ማሽን መማሪያ ሞዴልን ለማስተዋወቅ ረጅም ብሎግ ጻፍ። ቢያንስ 3 አንቀጾች መሆን አለባቸው።


2024-04-21 19:29:03.870348: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-04-21 19:29:03.870468: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-04-21 19:29:04.015708: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


the inference time is 24114.041730000055 ms
MODEL_OUTPUT: Below is an interaction between a human and an AI fluent in English and Amharic, providing reliable and informative answers.
The AI is supposed to answer test questions from the human with short responses saying just the answer and nothing else.
Human: አማርኛ መናገር የሚችል ማሽን መማሪያ ሞዴልን ለማስተዋወቅ ረጅም ብሎግ ጻፍ። ቢያንስ 3 አንቀጾች መሆን አለባቸው።
Assistant [Amharic] : 🎉አስደሳች ዜና! አማርኛ መናገር የሚችል የማሽን መማሪያ ሞዴልን ማስተዋወቅ! ይህ ሞዴል የተነደፈው ኢትዮጵያውያን እና ሌሎች የአፍሪካ ቋንቋዎችን አቀላጥፎ መናገር ለሚችሉ


KeyboardInterrupt: Interrupted by user

Type question in Amharic or English:  
